In [51]:
!pip3 install datawig

Processing c:\users\rupal\appdata\local\pip\cache\wheels\9b\a2\80\f3c44c1e8357a5ef3e85a0fd7a323511266ec42762d91e1025\datawig-0.1.12-cp36-none-any.whl
  Using cached https://files.pythonhosted.org/packages/4a/bd/eee1157fc2d8514970b345d69cb9975dcd1e42cd7e61146ed841f6e68309/typing-3.6.6-py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/f0/ac/92c3d2f0b627efbd1a7b2156faa697f9c2bbd7b0fe83ba8a9d36f982156f/pandas-0.25.3-cp36-cp36m-win_amd64.whl
  Using cached https://files.pythonhosted.org/packages/d0/19/6d56792b95445fc9b818e8d8eff3d5fff1221c40fe06a096c9587f2cb1d3/mxnet-1.4.0-py2.py3-none-win_amd64.whl
  Using cached https://files.pythonhosted.org/packages/49/df/50aa1999ab9bde74656c2919d9c0c085fd2b3775fd3eca826012bef76d8c/requests-2.18.4-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/53/39/4ab213673844e0c004bed8a0781a0721a3f6bb23eb8854ee75c236428892/graphviz-0.8.4-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/63/c

ERROR: py2neo 4.1.0 has requirement prompt-toolkit==1.0.15, but you'll have prompt-toolkit 2.0.7 which is incompatible.
ERROR: mxnet 1.4.0 has requirement numpy<1.15.0,>=1.8.2, but you'll have numpy 1.16.4 which is incompatible.
ERROR: Could not install packages due to an EnvironmentError: [WinError 5] Access is denied: 'd:\\users\\rupal\\anaconda3\\lib\\site-packages\\~andas\\io\\msgpack\\_packer.cp36-win_amd64.pyd'
Consider using the `--user` option or check the permissions.

You should consider upgrading via the 'python -m pip install --upgrade pip' command.


In [1]:
import pandas as pd
import numpy as np

from pandas_profiling import ProfileReport

from jenga.tasks.income import IncomeEstimationTask
from jenga.corruptions.generic import MissingValues
from jenga.evaluation.corruption_impact import CorruptionImpactEvaluator

import datawig

#### Data

In [2]:
dat = IncomeEstimationTask(seed=10)

In [3]:
train_dat = dat.train_data
train_lab = dat.train_labels

In [4]:
print(type(train_dat))
print(type(train_lab))

<class 'pandas.core.frame.DataFrame'>
<class 'numpy.ndarray'>


In [5]:
train_dat.head()

workclass       occupation      marital_status     education  \
5514          Local-gov   Prof-specialty       Never-married     Bachelors   
19777           Private  Exec-managerial  Married-civ-spouse     Assoc-voc   
10781  Self-emp-not-inc     Craft-repair           Separated           9th   
32240           Private  Farming-fishing  Married-civ-spouse     Assoc-voc   
9876            Private    Other-service            Divorced  Some-college   

       hours_per_week  age  
5514               50   33  
19777              50   36  
10781              40   58  
32240              46   21  
9876               40   27

In [46]:
profile = ProfileReport(train_dat, title="Training Data Profiling Report")
profile

Workclass and Occupation are the only columns with missing values in the training data

In [8]:
train_lab[0:5]

array([ True,  True, False, False, False])

In [9]:
test_dat = dat.test_data

In [39]:
test_dat.isnull().sum()

workclass         389
occupation        389
marital_status      0
education           0
hours_per_week      0
age                 0
dtype: int64

Workclass and Occupation are the only columns with missing values also in the test data

#### Simple Model

In [10]:
# fit a baseline model
model = dat.fit_baseline_model(train_dat, train_lab)

Fitting 5 folds for each of 12 candidates, totalling 60 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done  42 tasks      | elapsed:   11.0s
[Parallel(n_jobs=-1)]: Done  60 out of  60 | elapsed:   12.3s finished


In [11]:
# get the prediction probability estimates on the test set
pred_prob = model.predict_proba(test_dat)
dat.score_on_test_data(pred_prob) ## function from the base class "BinaryClassificationTask"
## score: roc_auc_score from sklearn.metrics

0.8818203960338398

#### Test on corrupted data

In [12]:
# corrupt the test data
missing_values_corruption = MissingValues(column="age", fraction=0.45, missingness="MAR", na_value=999)

corrupt_test_dat = missing_values_corruption.transform(test_dat)
corrupt_test_dat

workclass         occupation      marital_status     education  \
14160           Private       Adm-clerical            Divorced  Some-college   
27048         State-gov    Exec-managerial  Married-civ-spouse       HS-grad   
28868           Private    Exec-managerial  Married-civ-spouse     Bachelors   
5667            Private  Machine-op-inspct       Never-married     Bachelors   
7827   Self-emp-not-inc       Craft-repair            Divorced  Some-college   
...                 ...                ...                 ...           ...   
1338            Private       Tech-support            Divorced     Bachelors   
24534         Local-gov     Prof-specialty  Married-civ-spouse  Some-college   
18080           Private     Prof-specialty  Married-civ-spouse   Prof-school   
10354           Private       Adm-clerical       Never-married     Bachelors   
24639           Private      Other-service       Never-married       HS-grad   

       hours_per_week  age  
14160              38  999  
27048              40   45  
28868              55   29  
5667               40   30  
7827               50   29  
...               ...  ...  
1338               16  999  
24534              40   55  
18080              48  999  
10354              40  999  
24639              25  999  

[6513 rows x 6 columns]

In [13]:
# get the prediction probability estimates on the corrupted test set
pred_prob_currupt = model.predict_proba(corrupt_test_dat)
dat.score_on_test_data(pred_prob_currupt)

0.6639485891207517

#### Evaluate the impact of corruptions on the baseline model
using the evaluator from Jenga

In [14]:
# corruption impact evaluator
evaluator = CorruptionImpactEvaluator(dat)

num_repetitions = 10
results = evaluator.evaluate(model, num_repetitions, missing_values_corruption)

0/10 (0.046875)


In [15]:
results

In [16]:
print(f"""
Score (AUC) on
    data: {results[0].baseline_score}
    corrupted data: {np.mean(results[0].corrupted_scores)}
""")


Score (AUC) on
    data: 0.8818203960338398
    corrupted data: 0.6877612191942123



In [ ]:
### analyse the result
### see how the evaluator works
### analyse the difference in scores using evaluator and predict_proba

#### Try imputing the columns with missing values using Datawig

In [17]:
## training imputation models for the columns with null values: workclass and occupation
## both are categorical attributes

# workclass
workclass_imputer = datawig.SimpleImputer(
    input_columns=['occupation', 'marital_status', 'education'],
    output_column='workclass',
    output_path='imputer_model_workclass')

workclass_imputer.fit(train_dat)

2020-06-04 13:36:31,875 [INFO]  CategoricalEncoder for column workclass                                found only 9 occurrences of value Without-pay
2020-06-04 13:36:31,875 [INFO]  CategoricalEncoder for column workclass                                found only 5 occurrences of value Never-worked
2020-06-04 13:36:42,237 [INFO]  
========== start: fit model
2020-06-04 13:36:42,237 [WARNING]  Already bound, ignoring bind()
2020-06-04 13:37:01,157 [INFO]  Epoch[0] Batch [0-692]	Speed: 587.36 samples/sec	cross-entropy=0.875953	workclass-accuracy=0.732774
2020-06-04 13:37:25,965 [INFO]  Epoch[0] Train-cross-entropy=0.843141
2020-06-04 13:37:25,973 [INFO]  Epoch[0] Train-workclass-accuracy=0.738530
2020-06-04 13:37:25,975 [INFO]  Epoch[0] Time cost=43.723
2020-06-04 13:37:25,996 [INFO]  Saved checkpoint to "imputer_model_workclass\model-0000.params"
2020-06-04 13:37:31,157 [INFO]  Epoch[0] Validation-cross-entropy=0.809481
2020-06-04 13:37:31,166 [INFO]  Epoch[0] Validation-workclass-accura

In [18]:
# occupation
occupation_imputer = datawig.SimpleImputer(
    input_columns=['workclass', 'marital_status', 'education'],
    output_column='occupation',
    output_path='imputer_model_occupation')

occupation_imputer.fit(train_dat)

2020-06-04 13:46:36,111 [INFO]  CategoricalEncoder for column occupation                                found only 6 occurrences of value Armed-Forces
2020-06-04 13:46:47,649 [WARNING]  Test set does not contain any ocurrences of values [Armed-Forces] in column [occupation], consider using a more representative test set.
2020-06-04 13:46:47,671 [INFO]  
========== start: fit model
2020-06-04 13:46:47,671 [WARNING]  Already bound, ignoring bind()
2020-06-04 13:47:14,721 [INFO]  Epoch[0] Batch [0-692]	Speed: 410.84 samples/sec	cross-entropy=1.984914	occupation-accuracy=0.277597
2020-06-04 13:47:38,465 [INFO]  Epoch[0] Train-cross-entropy=1.941410
2020-06-04 13:47:38,465 [INFO]  Epoch[0] Train-occupation-accuracy=0.285856
2020-06-04 13:47:38,465 [INFO]  Epoch[0] Time cost=50.779
2020-06-04 13:47:38,503 [INFO]  Saved checkpoint to "imputer_model_occupation\model-0000.params"
2020-06-04 13:47:41,295 [INFO]  Epoch[0] Validation-cross-entropy=1.882041
2020-06-04 13:47:41,295 [INFO]  Epoch[0] 

In [19]:
## impute the columns in the training data
imputed = workclass_imputer.predict(train_dat)

In [20]:
imputed_copy = imputed.copy(deep=True)
imputed_copy

workclass       occupation      marital_status     education  \
5514          Local-gov   Prof-specialty       Never-married     Bachelors   
19777           Private  Exec-managerial  Married-civ-spouse     Assoc-voc   
10781  Self-emp-not-inc     Craft-repair           Separated           9th   
32240           Private  Farming-fishing  Married-civ-spouse     Assoc-voc   
9876            Private    Other-service            Divorced  Some-college   
...                 ...              ...                 ...           ...   
29802           Private     Craft-repair  Married-civ-spouse     Bachelors   
5390            Private    Other-service            Divorced          12th   
860             Private     Adm-clerical       Never-married          11th   
15795  Self-emp-not-inc  Farming-fishing  Married-civ-spouse       HS-grad   
23654      Self-emp-inc  Farming-fishing            Divorced     Bachelors   

       hours_per_week  age workclass_imputed  workclass_imputed_proba  
5514               50   33           Private                 0.677855  
19777              50   36           Private                 0.674601  
10781              40   58           Private                 0.849764  
32240              46   21  Self-emp-not-inc                 0.556772  
9876               40   27           Private                 0.805980  
...               ...  ...               ...                      ...  
29802              40   47           Private                 0.728300  
5390               21   31           Private                 0.839129  
860                20   18           Private                 0.888989  
15795              84   50  Self-emp-not-inc                 0.533733  
23654              60   34  Self-emp-not-inc                 0.447847  

[26048 rows x 8 columns]

In [21]:
# checking cases like index 11580 
imputed_copy.loc[imputed_copy["workclass"].isnull()& imputed_copy["occupation"].isnull()]

workclass occupation      marital_status     education  hours_per_week  \
28175       NaN        NaN       Never-married       HS-grad              60   
2359        NaN        NaN       Never-married          10th              40   
18846       NaN        NaN       Never-married  Some-college              40   
23176       NaN        NaN       Never-married       HS-grad              20   
24461       NaN        NaN  Married-civ-spouse       HS-grad              60   
...         ...        ...                 ...           ...             ...   
3005        NaN        NaN       Never-married  Some-college              30   
18942       NaN        NaN           Separated       HS-grad              20   
23333       NaN        NaN       Never-married          11th              40   
8322        NaN        NaN       Never-married  Some-college              30   
28020       NaN        NaN  Married-civ-spouse           9th              40   

       age workclass_imputed  workclass_imputed_proba  
28175   19      Never-worked                 0.993153  
2359    20      Never-worked                 0.998881  
18846   33      Never-worked                 0.985267  
23176   18      Never-worked                 0.993153  
24461   49      Never-worked                 0.978550  
...    ...               ...                      ...  
3005    19      Never-worked                 0.985267  
18942   18      Never-worked                 0.655034  
23333   17      Never-worked                 0.976416  
8322    20      Never-worked                 0.985267  
28020   66      Never-worked                 0.939516  

[1447 rows x 8 columns]

In [22]:
imputed.loc[imputed["workclass"].isnull(), "workclass"] = imputed["workclass" + '_imputed']

In [23]:
imputed.loc[imputed["workclass"].isnull()]

Empty DataFrame
Columns: [workclass, occupation, marital_status, education, hours_per_week, age, workclass_imputed, workclass_imputed_proba]
Index: []

In [24]:
imputed

workclass       occupation      marital_status     education  \
5514          Local-gov   Prof-specialty       Never-married     Bachelors   
19777           Private  Exec-managerial  Married-civ-spouse     Assoc-voc   
10781  Self-emp-not-inc     Craft-repair           Separated           9th   
32240           Private  Farming-fishing  Married-civ-spouse     Assoc-voc   
9876            Private    Other-service            Divorced  Some-college   
...                 ...              ...                 ...           ...   
29802           Private     Craft-repair  Married-civ-spouse     Bachelors   
5390            Private    Other-service            Divorced          12th   
860             Private     Adm-clerical       Never-married          11th   
15795  Self-emp-not-inc  Farming-fishing  Married-civ-spouse       HS-grad   
23654      Self-emp-inc  Farming-fishing            Divorced     Bachelors   

       hours_per_week  age workclass_imputed  workclass_imputed_proba  
5514               50   33           Private                 0.677855  
19777              50   36           Private                 0.674601  
10781              40   58           Private                 0.849764  
32240              46   21  Self-emp-not-inc                 0.556772  
9876               40   27           Private                 0.805980  
...               ...  ...               ...                      ...  
29802              40   47           Private                 0.728300  
5390               21   31           Private                 0.839129  
860                20   18           Private                 0.888989  
15795              84   50  Self-emp-not-inc                 0.533733  
23654              60   34  Self-emp-not-inc                 0.447847  

[26048 rows x 8 columns]

Notice update for the index 11580

In [25]:
# maintaining the structure of the imputed df the same as the training df
imputed[train_dat.columns]

workclass       occupation      marital_status     education  \
5514          Local-gov   Prof-specialty       Never-married     Bachelors   
19777           Private  Exec-managerial  Married-civ-spouse     Assoc-voc   
10781  Self-emp-not-inc     Craft-repair           Separated           9th   
32240           Private  Farming-fishing  Married-civ-spouse     Assoc-voc   
9876            Private    Other-service            Divorced  Some-college   
...                 ...              ...                 ...           ...   
29802           Private     Craft-repair  Married-civ-spouse     Bachelors   
5390            Private    Other-service            Divorced          12th   
860             Private     Adm-clerical       Never-married          11th   
15795  Self-emp-not-inc  Farming-fishing  Married-civ-spouse       HS-grad   
23654      Self-emp-inc  Farming-fishing            Divorced     Bachelors   

       hours_per_week  age  
5514               50   33  
19777              50   36  
10781              40   58  
32240              46   21  
9876               40   27  
...               ...  ...  
29802              40   47  
5390               21   31  
860                20   18  
15795              84   50  
23654              60   34  

[26048 rows x 6 columns]

In [ ]:
## impute the columns in the training data
def impute_dat(data, imputers):
    imputed = data.copy(deep=True)
    for imputer in imputers:
        imputed = imputer.predict(imputed, inplace=True)
    
    return imputed

In [26]:
## impute the columns in the training data
def impute_dat(data, columns, imputers):
    imputed = data.copy(deep=True)
    for imputer in imputers:
        imputed = imputer.predict(imputed, inplace=True)
    
    for column in columns:
        imputed.loc[imputed[column].isnull(), column] = imputed[column + '_imputed']
    
    return imputed[data.columns]

In [27]:
## impute the training data for missing values in "workclass" and "occupation"
train_dat_imputed = impute_dat(train_dat, ["workclass", "occupation"],[workclass_imputer, occupation_imputer])

In [28]:
train_dat_imputed

workclass       occupation      marital_status     education  \
5514          Local-gov   Prof-specialty       Never-married     Bachelors   
19777           Private  Exec-managerial  Married-civ-spouse     Assoc-voc   
10781  Self-emp-not-inc     Craft-repair           Separated           9th   
32240           Private  Farming-fishing  Married-civ-spouse     Assoc-voc   
9876            Private    Other-service            Divorced  Some-college   
...                 ...              ...                 ...           ...   
29802           Private     Craft-repair  Married-civ-spouse     Bachelors   
5390            Private    Other-service            Divorced          12th   
860             Private     Adm-clerical       Never-married          11th   
15795  Self-emp-not-inc  Farming-fishing  Married-civ-spouse       HS-grad   
23654      Self-emp-inc  Farming-fishing            Divorced     Bachelors   

       hours_per_week  age  
5514               50   33  
19777              50   36  
10781              40   58  
32240              46   21  
9876               40   27  
...               ...  ...  
29802              40   47  
5390               21   31  
860                20   18  
15795              84   50  
23654              60   34  

[26048 rows x 6 columns]

In [40]:
## impute the test data for missing values in "workclass" and "occupation"
test_dat_imputed = impute_dat(test_dat, ["workclass", "occupation"],[workclass_imputer, occupation_imputer])

In [41]:
test_dat_imputed

workclass         occupation      marital_status     education  \
14160           Private       Adm-clerical            Divorced  Some-college   
27048         State-gov    Exec-managerial  Married-civ-spouse       HS-grad   
28868           Private    Exec-managerial  Married-civ-spouse     Bachelors   
5667            Private  Machine-op-inspct       Never-married     Bachelors   
7827   Self-emp-not-inc       Craft-repair            Divorced  Some-college   
...                 ...                ...                 ...           ...   
1338            Private       Tech-support            Divorced     Bachelors   
24534         Local-gov     Prof-specialty  Married-civ-spouse  Some-college   
18080           Private     Prof-specialty  Married-civ-spouse   Prof-school   
10354           Private       Adm-clerical       Never-married     Bachelors   
24639           Private      Other-service       Never-married       HS-grad   

       hours_per_week  age  
14160              38   27  
27048              40   45  
28868              55   29  
5667               40   30  
7827               50   29  
...               ...  ...  
1338               16   71  
24534              40   55  
18080              48   47  
10354              40   27  
24639              25   18  

[6513 rows x 6 columns]

#### Fit the baseline model on the imputed data
Need to impute the test data as well? 

In [29]:
model_imputed = dat.fit_baseline_model(train_dat_imputed, train_lab)

Fitting 5 folds for each of 12 candidates, totalling 60 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done  42 tasks      | elapsed:    9.7s
[Parallel(n_jobs=-1)]: Done  60 out of  60 | elapsed:   11.0s finished


In [30]:
# get the prediction probability estimates on the test set
pred_prob_imputed = model_imputed.predict_proba(test_dat)
dat.score_on_test_data(pred_prob_imputed)

0.8767631321547648

In [31]:
# get the prediction probability estimates on the corrupted test set - makes sense?
pred_prob_imputed_corrupt = model_imputed.predict_proba(corrupt_test_dat)
dat.score_on_test_data(pred_prob_imputed_corrupt)

0.6605410154353195

### Scenarios from the CleanML paper

(Some repetitions from above may be here)

Given a dataset with a train/test split and a cleaning method, we can have different model performance depending on where the cleaning is performed

#### Cases

In [ ]:
## model: model trained on the original "dirty" training data
## model_imputed: model trained on the cleaned (imputed) training data

In [42]:
## Case A: model built using the original dirty training set and tested on the original dirty training set
dat.score_on_test_data(model.predict_proba(test_dat))

0.8818203960338398

In [43]:
## Case B: model built using the original dirty training set and tested on the cleaned test set
dat.score_on_test_data(model.predict_proba(test_dat_imputed))

0.8803161227849676

In [44]:
## Case C: model built using cleaned training set and tested on the original dirty test set
dat.score_on_test_data(model_imputed.predict_proba(test_dat))

0.8767631321547648

In [45]:
## Case D: model built using the cleaned training set and tested on the cleaned test set
dat.score_on_test_data(model_imputed.predict_proba(test_dat_imputed))

0.8789458031433245

Goal: compare two of the above cases to evaluate how cleaning affects model performance

#### Scenarios

Scenario BD: 
* Shows the effects of cleaning dirty data in the training set when the models are evaluated on the clean test set.
* Reflective of the real-world model building phase, where we are given a dirty training set and we would like to know whether we need to clean the training set.
* Ofc, in order to test whether cleaning training data helps, the two models need to be evaluated on the same cleaned test data.

Scenario CD:
* Shows the effects of cleaning dirty data in the test set when the models are trained on the cleaned training set.
* Reflective of the real-world model deployment phase, where the model is deployed and is being used for new test data, and we would like to know whether cleaning incoming dirty test data helps with the predictive performance

### Credit dataset

In [65]:
cs_train = pd.read_csv("../Data/GiveMeSomeCredit/cs-training.csv")

In [66]:
cs_train.drop(['Unnamed: 0'], axis=1, inplace=True)
cs_train

SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines  age  \
0                      1                              0.766127   45   
1                      0                              0.957151   40   
2                      0                              0.658180   38   
3                      0                              0.233810   30   
4                      0                              0.907239   49   
...                  ...                                   ...  ...   
149995                 0                              0.040674   74   
149996                 0                              0.299745   44   
149997                 0                              0.246044   58   
149998                 0                              0.000000   30   
149999                 0                              0.850283   64   

        NumberOfTime30-59DaysPastDueNotWorse    DebtRatio  MonthlyIncome  \
0                                          2     0.802982         9120.0   
1                                          0     0.121876         2600.0   
2                                          1     0.085113         3042.0   
3                                          0     0.036050         3300.0   
4                                          1     0.024926        63588.0   
...                                      ...          ...            ...   
149995                                     0     0.225131         2100.0   
149996                                     0     0.716562         5584.0   
149997                                     0  3870.000000            NaN   
149998                                     0     0.000000         5716.0   
149999                                     0     0.249908         8158.0   

        NumberOfOpenCreditLinesAndLoans  NumberOfTimes90DaysLate  \
0                                    13                        0   
1                                     4                        0   
2                                     2                        1   
3                                     5                        0   
4                                     7                        0   
...                                 ...                      ...   
149995                                4                        0   
149996                                4                        0   
149997                               18                        0   
149998                                4                        0   
149999                                8                        0   

        NumberRealEstateLoansOrLines  NumberOfTime60-89DaysPastDueNotWorse  \
0                                  6                                     0   
1                                  0                                     0   
2                                  0                                     0   
3                                  0                                     0   
4                                  1                                     0   
...                              ...                                   ...   
149995                             1                                     0   
149996                             1                                     0   
149997                             1                                     0   
149998                             0                                     0   
149999                             2                                     0   

        NumberOfDependents  
0                      2.0  
1                      1.0  
2                      0.0  
3                      0.0  
4                      0.0  
...                    ...  
149995                 0.0  
149996                 2.0  
149997                 0.0  
149998                 0.0  
149999                 0.0  

[150000 rows x 11 columns]

In [70]:
profile = ProfileReport(cs_train, title="Training Data Profiling Report")
profile

In [67]:
cs_test = pd.read_csv("../Data/GiveMeSomeCredit/cs-test.csv")

In [69]:
cs_test.drop(['Unnamed: 0'], axis=1, inplace=True)
cs_test

SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines  age  \
0                    NaN                              0.885519   43   
1                    NaN                              0.463295   57   
2                    NaN                              0.043275   59   
3                    NaN                              0.280308   38   
4                    NaN                              1.000000   27   
...                  ...                                   ...  ...   
101498               NaN                              0.282653   24   
101499               NaN                              0.922156   36   
101500               NaN                              0.081596   70   
101501               NaN                              0.335457   56   
101502               NaN                              0.441842   29   

        NumberOfTime30-59DaysPastDueNotWorse    DebtRatio  MonthlyIncome  \
0                                          0     0.177513         5700.0   
1                                          0     0.527237         9141.0   
2                                          0     0.687648         5083.0   
3                                          1     0.925961         3200.0   
4                                          0     0.019917         3865.0   
...                                      ...          ...            ...   
101498                                     0     0.068522         1400.0   
101499                                     3     0.934217         7615.0   
101500                                     0   836.000000            NaN   
101501                                     0  3568.000000            NaN   
101502                                     0     0.198918         5916.0   

        NumberOfOpenCreditLinesAndLoans  NumberOfTimes90DaysLate  \
0                                     4                        0   
1                                    15                        0   
2                                    12                        0   
3                                     7                        0   
4                                     4                        0   
...                                 ...                      ...   
101498                                5                        0   
101499                                8                        0   
101500                                3                        0   
101501                                8                        0   
101502                               12                        0   

        NumberRealEstateLoansOrLines  NumberOfTime60-89DaysPastDueNotWorse  \
0                                  0                                     0   
1                                  4                                     0   
2                                  1                                     0   
3                                  2                                     0   
4                                  0                                     0   
...                              ...                                   ...   
101498                             0                                     0   
101499                             2                                     0   
101500                             0                                     0   
101501                             2                                     1   
101502                             0                                     0   

        NumberOfDependents  
0                      0.0  
1                      2.0  
2                      2.0  
3                      0.0  
4                      1.0  
...                    ...  
101498                 0.0  
101499                 4.0  
101500                 NaN  
101501                 3.0  
101502                 0.0  

[101503 rows x 11 columns]

### EXTRAS

#### Glue code (decorators) to be able to apply imputers
(taken from the sikm-submi.... notebook)

In [31]:
class ModelDecorator:
    def __init__(self, model, target_column, imputers):
        self.model = model
        self.imputers = imputers
        
    def predict_proba(self, data):
        imputed = data
        for imputer in self.imputers:
            imputed = imputer.transform(imputed)
            
        return self.model.predict_proba(imputed)

In [32]:
## we already have a baseline model, here I'm creating a model with datawig imputers
datawig_model = ModelDecorator(model, [workclass_imputer, occupation_imputer])

#### Evaluate the impact of corruptions on the model with datawig imputation

In [33]:
results_decorated = evaluator.evaluate(datawig_model, num_repetitions, missing_values_corruption)

AttributeError: 'SimpleImputer' object has no attribute 'transform'

#### Checking the other tasks' data if they had any missing values to begin with 
(Just checking for some confusion)

In [71]:
from jenga.tasks.reviews import VideogameReviewsTask

profile = ProfileReport(VideogameReviewsTask(seed=10).train_data, title="Training Data Profiling Report")
profile

In [72]:
from jenga.tasks.shoes import ShoeCategorizationTask

profile = ProfileReport(ShoeCategorizationTask(seed=10).train_data, title="Training Data Profiling Report")
profile

Using TensorFlow backend.


4423680/4422102 [==============================] - 2s 0us/step


AttributeError: 'numpy.ndarray' object has no attribute 'index'